In [1]:
import torch
import yaml
import os

# Humandoid MARL
from Humanoid_MARL.envs.base_env import GymWrapper, VectorGymWrapper
from Humanoid_MARL.utils.torch_utils import save_models, load_models
from Humanoid_MARL.agent.ppo.train_torch import Agent, eval_unroll, get_agent_actions
from Humanoid_MARL.envs.torch_wrapper import TorchWrapper
from IPython.display import HTML, clear_output
from brax.io import html
import jax
from Humanoid_MARL import envs
from Humanoid_MARL.utils.utils import load_reward_config, load_config

In [2]:
env_name = "ants"
config = load_config(env_name)
env = envs.create(config['env_name'], auto_reset=True, **config['env_config'])
env = GymWrapper(env, get_jax_state=True)
env = TorchWrapper(env, device=config['train_config']['device'], get_jax_state=True)

model_path = os.path.join("../", config['train_config']['model_path'])
# env warmup
observation = env.reset()
action = torch.zeros(env.action_space.shape[0] * env.num_agents).to(config['train_config']['device'])
env.step(action)
agents = load_models(model_path, Agent, device=config['train_config']['device'])
jax_states = []
num_steps = 1000

eval_reward = 0.0
episodes = torch.zeros((), device = config['train_config']['device'])
for i in range(num_steps):
    print(f"{i} / {num_steps}")
    logits, action = get_agent_actions(agents, observation, env.obs_dims)
    if config['agent_config'].get("freeze_idx"):
        action[:,config['agent_config'].get("freeze_idx") * 17:(config['agent_config'].get("freeze_idx") * 17) + 17] =  torch.ones_like(action[:,config['agent_config'].get("freeze_idx") * 17:(config['agent_config'].get("freeze_idx") * 17) + 17]) * 0.01
    jax_state, observation, reward, done, info = env.step(Agent.dist_postprocess(action[0]))
    episodes += torch.sum(done)
    jax_states.append(jax_state)
    print(f"{i} | {info} | DONE [{done}] | Reward [{reward}]")
    eval_reward += reward
print(f"Total Reward | {eval_reward / episodes}")

Models loaded from ../models/20240329_150029_ppo_ants.pt
0 / 1000
0 | {'distance_from_origin': tensor([0.0862, 1.1338], device='cuda:0'), 'first_obs': tensor([ 4.8164e-01,  1.0992e+00, -3.7828e-02,  1.6740e-02,  9.6863e-02,
         2.9342e-02,  9.1687e-01, -4.6309e-02, -1.0673e+00,  9.3469e-02,
        -1.0755e+00,  6.9031e-02,  9.4039e-01,  4.5651e-01,  1.0069e+00,
        -3.1048e-02,  2.4030e-02, -2.6170e-02,  1.6610e-02,  9.7779e-01,
         3.3736e-05, -1.0207e+00,  6.5738e-03, -9.6481e-01, -3.4261e-02,
         9.0044e-01, -6.4604e-02,  2.6472e-02, -5.1049e-02, -9.4768e-02,
        -8.0044e-03,  1.4586e-01,  2.1858e-02,  1.4449e-01, -8.8535e-02,
         8.3774e-02, -7.8171e-02, -7.0983e-02, -3.1660e-02,  9.9085e-02,
         9.2387e-02,  1.6677e-01, -1.0610e-01,  1.5068e-01,  3.9902e-03,
         1.3045e-01,  3.9970e-02,  1.5674e-01, -9.1280e-02, -1.5586e-01,
        -7.9559e-04, -1.1222e-01, -1.1123e-01, -4.6891e-02], device='cuda:0'), 'first_pipeline_state': None, 'forward_r

In [3]:
HTML(html.render(env.sys, [jax_state.pipeline_state for jax_state in jax_states])) 

In [4]:
HTML(html.render(env.sys, [jax_state.pipeline_state for jax_state in jax_states])) 

: 